# Composição Temporal
- Teste para agrupamento de imagens por intervalo temporal
- Este notebook irá demonstrar como agrupar as imagens coletadas por mês

In [1]:
import ee
import geemap
import sys
import os
sys.path.append(os.path.abspath(os.path.join(os.getcwd(),os.pardir)))
from src import eetools as eet

In [2]:
try: 
    ee.Initialize()
except:
    ee.Authenticate()
    ee.Initialize()

In [3]:
coordenadas = "-48.53801472648439,-22.503806214013736,-48.270222978437516,-22.7281869567509"
x1, y1, x2, y2 = coordenadas.split(",")

datas = "2013-01-01,2018-12-01"
inicio, fim = datas.split(",")
escala = 30

geom = ee.Geometry.Polygon([[[float(x1),float(y2)],
                             [float(x2),float(y2)],
                             [float(x2),float(y1)],
                             [float(x1),float(y1)],
                             [float(x1),float(y2)]]])

latitude_central = (float(x1)+float(x2))/2
longitude_central = (float(y1)+float(y2))/2

In [4]:
collec = ee.ImageCollection('LANDSAT/LC08/C01/T1_SR')\
    .filterBounds(geom)\
    .filterDate(inicio,fim)\
    .filterMetadata('CLOUD_COVER','less_than',30)

In [10]:
collec_ndvi = collec.map(eet.ndvi)

In [83]:
years = ee.List.sequence(2013,2018)

In [12]:
collec_ndvi

In [120]:
composite = ee.ImageCollection(
    years.map(
        lambda y: collec_ndvi\
            .filter(ee.Filter.calendarRange(y,y,'year'))\
            .median()\
            .set("year",y,"system:id",y)\
            .set("system:index",ee.Number(y).format("%04d"))
    )
)

composite

In [121]:
composite.select('ndvi').toBands()